In [ ]:
import sys
from pathlib import Path
import numpy as np
from scipy.interpolate import griddata
import matplotlib.pyplot as plt
import laspy

triskele_path = Path('../triskele/python/')
sys.path.append(str(triskele_path.resolve()))
import triskele

figsize = np.array((16, 3)) * 1.5

# Setup

## Load LiDAR data

In [ ]:
def find_las(path):
    path = Path(path)
    las = list()
    
    if path.is_dir():
        for child in path.iterdir():
            las.extend(find_las(child))
    
    if path.is_file() and path.suffix == '.las':
        las.append(path)
    
    return las

In [ ]:
def auto_filter(data, treshold=.5):
    tresholds = np.percentile(data, [treshold, 100 - treshold])

    data[data < tresholds[0]] = tresholds[0]
    data[data > tresholds[1]] = tresholds[1]

In [ ]:
def bulk_load(path, name=None):
    data = {'file': path, 'name': name}

    attributes = ['x', 'y', 'z', 'intensity', 'num_returns', 'scan_angle_rank', 'pt_src_id', 'gps_time']
    for a in attributes:
        data[a] = list()
        
    print('Load data...')
    for f in find_las(path):
        print('{}: '.format(f), end='')
        infile = laspy.file.File(f)
        for i, a in enumerate(attributes):
            print('\r {}: [{:3d}%]'.format(f, int(i/len(attributes) * 100)), end='')
            data[a].extend(getattr(infile, a))
        infile.close()
        print('\r {}: [Done]'.format(f))

    
    print('Create matrices...', end='')
    for i, a in enumerate(attributes):
        print('\rCreate matrices: [{:3d}%]'.format(int(i/len(attributes) * 100)), end='')
        data[a] = np.array(data[a])
    print('\rCreate matrices: [Done]')
        
    print('Filter data...', end='')
    for i, a in enumerate(attributes):
        print('\rFilter data: [{:3d}%]'.format(int(i/len(attributes) * 100)), end='')
        if a == 'x' or a == 'y':
            continue
        auto_filter(data[a])
    print('\rFilter data: [Done]')

    return data

In [ ]:
C1 = bulk_load('../Data/lidar/C1/', 'C1')
C2 = bulk_load('../Data/lidar/C2/', 'C2')
C3 = bulk_load('../Data/lidar/C3/', 'C3')
C123 = bulk_load('../Data/lidar/', 'C123') # Todo: Copy C1 C2 C3

## Define raster function

In [ ]:
def rasterize(coords, values, resolution=1, method='nearest'):
    if isinstance(coords, np.ndarray):
        xmin, xmax = coords[:,0].min(), coords[:,0].max()
        ymin, ymax = coords[:,1].min(), coords[:,1].max()
    else:
        xmin, xmax = coords[0].min(), coords[0].max()
        ymin, ymax = coords[1].min(), coords[1].max()

    gridx, gridy = np.mgrid[xmin:xmax:resolution, ymin:ymax:resolution]
    
    return griddata(coords, values, (gridx, gridy), method=method).T # linear, nearest, cubic

In [ ]:
def raster_show_and_save(coords, values, resolution=1, method='nearest', name=None, save_dir='../Res'):
    """Display and save rasters. If name is provided, will try to cache result to reload it later."""
    
    if name is not None:
        base_name = '{}/{}'.format(save_dir, name)
        tiff_file = Path(base_name + '.tiff')
        png_file = Path(base_name + '.png')
        
    if name is not None and tiff_file.exists() :
        print ('WARNING: Loading cached result {}'.format(tiff_file))
        raster = triskele.read(tiff_file)
    else:         
        raster = rasterize(coords, values, resolution, method)
    
    plt.figure(figsize=figsize)
    plt.imshow(raster, origin='lower')
    plt.colorbar()
    plt.title(name)
    plt.show()
    
    if name is not None:
        plt.imsave(png_file, raster, origin='lower')
        triskele.write(tiff_file, raster)
        
    return raster

In [ ]:
def raster_assistant(data, field='z', resolution='1', method='nearest', weight_field=None):
    if weight_field is None:
        name = '{}_{}_{}_{}'.format(data['name'], field, str(resolution).replace('.', '_'), method)
        raster_show_and_save((data['x'], data['y']), data[field], resolution, method, name)
    else:
        name = '{}_{}_{}_{}_w{}'.format(data['name'], field, str(resolution).replace('.', '_'), method, weight_field)
        raster_show_and_save((data['x'], data['y']), data[field] * data[weight_field], resolution, method, name)

In [ ]:
def raster_assistant_mp(data, field='z', resolution='1', method='nearest', weight_field=None):
    if data == 'C1':
        raster_assistant(C1, field, resolution, method)
    if data == 'C2':
        raster_assistant(C2, field, resolution, method)
    if data == 'C3':
        raster_assistant(C3, field, resolution, method)
    if data == 'C123':
        raster_assistant(C123, field, resolution, method)

In [ ]:
rl = raster_assistant(C1, resolution=10)

# Interpolation Strategies for Global Griddata Rasterisation

## Fine textured (visible) rasters

### Nearest

In [ ]:
null = raster_assistant(C1, 'intensity', 0.5, 'nearest')

No interpolation, accurate values. On the downside, there is a lot of aliasing. Maybe that's because take all the points without selection on the z (altitude) axis.

### Linear

In [ ]:
null = raster_assistant(C1, 'intensity', 0.5, 'linear')

### Cubic

The results are pretty bad, same remark than before.

In [ ]:
null = raster_assistant(C1, 'intensity', 0.5, 'cubic')

The cubic create new values. Still, seems pretty useless with the aliasing. 

## Flat area (DSM) rasters

### Nearest

In [ ]:
null = raster_assistant(C1, 'z', 0.5, 'nearest')

No interpolation, accurate values. On the downside, there is a lot of aliasing. Maybe that's because take all the points without selection on the z (altitude) axis.

### Linear

In [ ]:
null = raster_assistant(C1, 'z', 0.5, 'linear')

### Cubic

The results are pretty bad, same remark than before.

In [ ]:
null = raster_assistant(C1, 'z', 0.5, 'cubic')

# Weight with altitude

## Visible

In [ ]:
null = raster_assistant(C1, 'intensity', 0.5, 'nearest', 'z')

In [ ]:
null = raster_assistant(C1, 'intensity', 0.5, 'linear', 'z')

## DSM

In [ ]:
null = raster_assistant(C1, 'z', 0.5, 'nearest', 'z')

In [ ]:
null = raster_assistant(C1, 'z', 0.5, 'linear', 'z')

# Other

In [ ]:
from multiprocessing import Pool, Process, Queue
import multiprocessing as mp
#mp.set_start_method('spawn')

pool = Pool(processes=20)

job_args = list()
for field in ('z', 'intensity', 'num_returns', 'gps_time'):
    for data in ('C1', 'C2', 'C3', 'C123'):
        job_args.append([data, field, 1, 'nearest'])
        
for i in pool.starmap(raster_assistant_mp, job_args):
    pass        